マウスの総移動距離を算出

import

In [2]:
import os
import math

関数の定義

In [35]:
def calculate_total_time(file_path):
    """
    指定されたファイルからタスクにかかった全体の時間を計算する
    ファイルから読み取る時間はミリ秒単位であるため、結果は秒単位で返します。
    """
    first_time = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # 特殊ケース: MENU_ITEM_NAVIGATED で "C:\\Users" を含む場合
                if line.startswith("MENU_ITEM_NAVIGATED") and "C:\\Users" in line:
                    parts = line.strip().rsplit(":", 1)
                    current_time = int(parts[-1].strip())
                else:
                    # 通常ケース: 2個目のコロンの後が時間
                    parts = line.strip().split(":")
                    if len(parts) > 2:
                        current_time = int(parts[2].strip())
                    else:
                        continue

                if first_time is None:
                    first_time = current_time
                last_time = current_time
            except Exception as e:
                print(f"Error processing line: {line}. Error: {e}")

    # ミリ秒から秒に変換
    total_time_seconds = (last_time - first_time) / 1000 if first_time is not None and last_time is not None else 0
    return total_time_seconds

def calculate_average_speed(file_path):
    """
    指定されたファイルからマウスの平均速度を計算する
    連続する"MOUSE_MOVED"または"MOUSE_DRAGGED"イベントのみを考慮。
    ファイルから読み取る時間はミリ秒単位であるため、時間を秒単位に変換します。
    """
    import math

    total_time = 0.0
    total_distance = 0.0
    last_position = None
    last_time = None
    mouse_event_flag = False

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            # マウスの移動に関する行を抽出
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x, y = map(int, parts[-1].strip().strip("()").split(","))
                    current_position = (x, y)
                    current_time = int(parts[-2].strip())

                    if mouse_event_flag and last_position is not None and last_time is not None:
                        # 前回の位置からの距離と経過時間を計算
                        distance = math.sqrt((current_position[0] - last_position[0])**2 +
                                             (current_position[1] - last_position[1])**2)
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        print(f"Distance: {distance}, Time Elapsed: {time_elapsed}")  # デバッグ用出力

                        total_distance += distance
                        total_time += time_elapsed

                    mouse_event_flag = True  # 現在の行がマウスイベントであることを記録
                    last_position = current_position
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")
            else:
                mouse_event_flag = False  # マウスイベントではない行があればフラグをリセット

    average_speed = total_distance / total_time if total_time > 0 else 0
    return average_speed


def calculate_average_X_direction_speed(file_path):
    """
    指定されたファイルからマウスのX方向の平均速度を計算する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: X方向の平均速度
    """
    total_time = 0.0
    total_x_distance = 0.0
    last_x = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            # マウスの移動に関する行を抽出
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x, _ = map(int, parts[-1].strip().strip("()").split(","))  # X座標のみ取得
                    current_x = x
                    current_time = int(parts[-2].strip())  # タイムスタンプ

                    if last_x is not None and last_time is not None:
                        # X方向の移動距離と経過時間を計算
                        x_distance = abs(current_x - last_x)  # X方向の移動量
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        total_x_distance += x_distance
                        total_time += time_elapsed

                    last_x = current_x
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    average_x_speed = total_x_distance / total_time if total_time > 0 else 0
    return average_x_speed

def calculate_average_Y_direction_speed(file_path):
    """
    指定されたファイルからマウスのY方向の平均速度を計算する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: Y方向の平均速度
    """
    total_time = 0.0
    total_y_distance = 0.0
    last_y = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            # マウスの移動に関する行を抽出
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    # 座標を取得
                    _, _, current_time_str, coordinates_str = parts
                    y = int(coordinates_str.strip().strip("()").split(",")[1].strip())  # Y座標のみ取得
                    current_y = y
                    current_time = int(current_time_str.strip())  # タイムスタンプ

                    if last_y is not None and last_time is not None:
                        # Y方向の移動距離と経過時間を計算
                        y_distance = abs(current_y - last_y)  # Y方向の移動量
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        total_y_distance += y_distance
                        total_time += time_elapsed

                    last_y = current_y
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line.strip()}. Error: {e}")

    average_y_speed = total_y_distance / total_time if total_time > 0 else 0
    return average_y_speed

def calculate_max_x_speed(file_path):
    """
    指定されたファイルからマウスのX方向の最大速度を計算する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: X方向の最大速度
    """
    max_speed = 0.0  # 最大速度を格納する変数
    last_x = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            # マウスの移動に関する行を抽出
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x = int(parts[-1].strip().strip("()").split(",")[0])  # X座標のみ取得
                    current_x = x
                    current_time = int(parts[-2].strip())  # タイムスタンプ

                    if last_x is not None and last_time is not None:
                        # X方向の移動距離と経過時間を計算
                        x_distance = abs(current_x - last_x)  # X方向の移動量
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        if time_elapsed > 0:
                            speed = x_distance / time_elapsed  # 速度を計算
                            max_speed = max(max_speed, speed)  # 最大速度を更新

                    last_x = current_x
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    return max_speed

def calculate_max_y_speed(file_path):
    """
    指定されたファイルからマウスのY方向の最大速度を計算する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: Y方向の最大速度
    """
    max_speed = 0.0  # 最大速度を格納する変数
    last_y = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            # マウスの移動に関する行を抽出
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    y = int(parts[-1].strip().strip("()").split(",")[1])  # Y座標のみ取得
                    current_y = y
                    current_time = int(parts[-2].strip())  # タイムスタンプ

                    if last_y is not None and last_time is not None:
                        # Y方向の移動距離と経過時間を計算
                        y_distance = abs(current_y - last_y)  # Y方向の移動量
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        if time_elapsed > 0:
                            speed = y_distance / time_elapsed  # 速度を計算
                            max_speed = max(max_speed, speed)  # 最大速度を更新

                    last_y = current_y
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    return max_speed

def calculate_max_speed(file_path):
    """
    指定されたファイルからマウスの最大速度を計算する
    """
    max_speed = 0.0
    last_position = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            # マウスの移動に関する行を抽出
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x, y = map(int, parts[-1].strip().strip("()").split(","))
                    current_position = (x, y)
                    current_time = int(parts[-2].strip())

                    if last_position is not None and last_time is not None:
                        # 前回の位置からの距離と経過時間を計算
                        distance = math.sqrt((current_position[0] - last_position[0])**2 +
                                             (current_position[1] - last_position[1])**2)
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        if time_elapsed > 0:
                            # 現在の速度を計算
                            speed = distance / time_elapsed
                            # 最大速度を更新
                            max_speed = max(max_speed, speed)

                    last_position = current_position
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    return max_speed

def calculate_max_x_accel(file_path):
    """
    指定されたファイルからマウスのX方向の最大加速度を計算する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: X方向の最大加速度
    """
    velocities = []  # X方向の速度を格納
    last_x = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x = int(parts[-1].strip().strip("()").split(",")[0])  # X座標のみ取得
                    current_x = x
                    current_time = int(parts[-2].strip())  # タイムスタンプ

                    if last_x is not None and last_time is not None:
                        # X方向の速度を計算
                        x_distance = current_x - last_x  # X方向の移動距離
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        if time_elapsed > 0:
                            velocity = x_distance / time_elapsed
                            velocities.append(velocity)

                    last_x = current_x
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    # X方向の加速度を計算
    max_acceleration = 0.0  # 最大加速度を格納する変数
    for i in range(1, len(velocities)):
        acceleration = abs(velocities[i] - velocities[i-1])  # 加速度の絶対値
        max_acceleration = max(max_acceleration, acceleration)  # 最大加速度を更新

    return max_acceleration

def calculate_max_y_accel(file_path):
    """
    指定されたファイルからマウスのY方向の最大加速度を計算する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: Y方向の最大加速度
    """
    velocities = []  # Y方向の速度を格納
    last_y = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    y = int(parts[-1].strip().strip("()").split(",")[1])  # Y座標のみ取得
                    current_y = y
                    current_time = int(parts[-2].strip())  # タイムスタンプ

                    if last_y is not None and last_time is not None:
                        # Y方向の速度を計算
                        y_distance = current_y - last_y  # Y方向の移動距離
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        if time_elapsed > 0:
                            velocity = y_distance / time_elapsed
                            velocities.append(velocity)

                    last_y = current_y
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    # Y方向の加速度を計算
    max_acceleration = 0.0  # 最大加速度を格納する変数
    for i in range(1, len(velocities)):
        acceleration = abs(velocities[i] - velocities[i-1])  # 加速度の絶対値
        max_acceleration = max(max_acceleration, acceleration)  # 最大加速度を更新

    return max_acceleration

def calculate_average_absolute_acceleration(file_path):
    """
    指定されたファイルからマウスの加速度の絶対値の平均を計算する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: マウスの加速度の絶対値の平均（ピクセル/秒^2）
    """
    import math

    velocities = []
    times = []  # 各速度の時間を記録
    last_position = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x, y = map(int, parts[-1].strip().strip("()").split(","))
                    current_position = (x, y)
                    current_time = int(parts[-2].strip())

                    if last_position is not None and last_time is not None:
                        # 距離と時間差から速度を計算
                        distance = math.sqrt((current_position[0] - last_position[0])**2 +
                                             (current_position[1] - last_position[1])**2)
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換
                        if time_elapsed > 0:
                            velocity = distance / time_elapsed
                            velocities.append(velocity)
                            times.append(current_time / 1000.0)  # 秒単位で記録

                    last_position = current_position
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    absolute_accelerations = []
    for i in range(1, len(velocities)):
        time_diff = times[i] - times[i - 1]  # 正しい時間差を計算
        if time_diff > 0:
            acceleration = abs(velocities[i] - velocities[i - 1]) / time_diff
            absolute_accelerations.append(acceleration)

    average_absolute_acceleration = sum(absolute_accelerations) / len(absolute_accelerations) if absolute_accelerations else 0
    return average_absolute_acceleration

def avg_mouse_X_accel(file_path):
    """
    指定されたファイルからマウスのX方向の平均加速度の絶対値を計算する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: X方向の平均加速度の絶対値
    """
    velocities = []  # X方向の速度を格納
    last_x = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x = int(parts[-1].strip().strip("()").split(",")[0])  # X座標のみ取得
                    current_x = x
                    current_time = int(parts[-2].strip())  # タイムスタンプ

                    if last_x is not None and last_time is not None:
                        # X方向の速度を計算
                        x_distance = current_x - last_x  # X方向の移動距離
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        if time_elapsed > 0:
                            velocity = x_distance / time_elapsed
                            velocities.append(velocity)

                    last_x = current_x
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    # X方向の加速度（絶対値）を計算
    absolute_accelerations = []
    for i in range(1, len(velocities)):
        acceleration = abs(velocities[i] - velocities[i-1])  # 加速度の絶対値
        absolute_accelerations.append(acceleration)

    # 平均加速度の絶対値を計算
    average_absolute_acceleration = (
        sum(absolute_accelerations) / len(absolute_accelerations) if absolute_accelerations else 0
    )
    return average_absolute_acceleration

def avg_mouse_Y_accel(file_path):
    """
    指定されたファイルからマウスのY方向の平均加速度の絶対値を計算する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: Y方向の平均加速度の絶対値
    """
    velocities = []  # Y方向の速度を格納
    last_y = None
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    y = int(parts[-1].strip().strip("()").split(",")[1])  # Y座標のみ取得
                    current_y = y
                    current_time = int(parts[-2].strip())  # タイムスタンプ

                    if last_y is not None and last_time is not None:
                        # Y方向の速度を計算
                        y_distance = current_y - last_y  # Y方向の移動距離
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換

                        if time_elapsed > 0:
                            velocity = y_distance / time_elapsed
                            velocities.append(velocity)

                    last_y = current_y
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    # Y方向の加速度（絶対値）を計算
    absolute_accelerations = []
    for i in range(1, len(velocities)):
        acceleration = abs(velocities[i] - velocities[i-1])  # 加速度の絶対値
        absolute_accelerations.append(acceleration)

    # 平均加速度の絶対値を計算
    average_absolute_acceleration = (
        sum(absolute_accelerations) / len(absolute_accelerations) if absolute_accelerations else 0
    )
    return average_absolute_acceleration


def calculate_max_acceleration(file_path):
    """
    指定されたファイルからマウスの最大加速度を計算する
    """
    velocities = []
    last_position = None
    last_time = None
    first_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x, y = map(int, parts[-1].strip().strip("()").split(","))
                    current_position = (x, y)
                    current_time = int(parts[-2].strip())

                    if first_time is None:
                        first_time = current_time

                    if last_position is not None and last_time is not None:
                        # 距離と時間差から速度を計算
                        distance = math.sqrt((current_position[0] - last_position[0])**2 +
                                             (current_position[1] - last_position[1])**2)
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換
                        if time_elapsed > 0:
                            velocity = distance / time_elapsed
                            velocities.append(velocity)

                    last_position = current_position
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    accelerations = []
    for i in range(1, len(velocities)):
        acceleration = (velocities[i] - velocities[i-1]) / (last_time - first_time if last_time and first_time else 1)
        accelerations.append(acceleration)

    max_acceleration = max(accelerations) if accelerations else 0
    return max_acceleration

def calculate_min_acceleration(file_path):
    """
    指定されたファイルからマウスの最小加速度を計算する
    """
    velocities = []
    last_position = None
    last_time = None
    first_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x, y = map(int, parts[-1].strip().strip("()").split(","))
                    current_position = (x, y)
                    current_time = int(parts[-2].strip())

                    if first_time is None:
                        first_time = current_time

                    if last_position is not None and last_time is not None:
                        # 距離と時間差から速度を計算
                        distance = math.sqrt((current_position[0] - last_position[0])**2 +
                                             (current_position[1] - last_position[1])**2)
                        time_elapsed = (current_time - last_time) / 1000.0  # ミリ秒から秒に変換
                        if time_elapsed > 0:
                            velocity = distance / time_elapsed
                            velocities.append(velocity)

                    last_position = current_position
                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    accelerations = []
    for i in range(1, len(velocities)):
        acceleration = (velocities[i] - velocities[i-1]) / (last_time - first_time if last_time and first_time else 1)
        accelerations.append(acceleration)

    min_acceleration = min(accelerations) if accelerations else 0
    return min_acceleration

def calculate_distance(file_path):
    """
    指定されたファイルからマウスの総移動距離を計算する
    """
    total_distance = 0.0
    last_position = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            # マウスの移動に関する行を抽出
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    x, y = map(int, parts[-1].strip().strip("()").split(","))
                    current_position = (x, y)

                    if last_position is not None:
                        # 前回の位置からの距離を計算
                        distance = math.sqrt((current_position[0] - last_position[0])**2 +
                                             (current_position[1] - last_position[1])**2)
                        total_distance += distance

                    last_position = current_position
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")
    return total_distance

def calculate_mouse_sensible_pause_count(file_path, threshold=150):
    """
    指定されたファイルから一時停止が閾値（ミリ秒）を超えた回数を計算する
    """
    pause_count = 0
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    current_time = int(parts[-2].strip())

                    if last_time is not None:
                        time_elapsed = current_time - last_time
                        if time_elapsed > threshold:
                            pause_count += 1

                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    return pause_count

def calculate_all_sensible_pause_count(file_path, threshold=150):
    """
    指定されたファイルからすべてのイベント間の一時停止時間が
    閾値（ミリ秒）以上の場合のみ、その回数をカウントする

    Parameters:
        file_path (str): ログファイルのパス
        threshold (int): 一時停止時間の閾値（ミリ秒単位、デフォルト: 150）

    Returns:
        int: 閾値以上の一時停止時間の回数
    """
    timestamps = []
    pause_count = 0

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # 特殊ケース: MENU_ITEM_NAVIGATED で "C:\Users" を含む場合
                if line.startswith("MENU_ITEM_NAVIGATED") and "C:\\Users" in line:
                    parts = line.strip().rsplit(":", 1)
                    current_time = int(parts[-1].strip())
                else:
                    # 通常ケース: 2個目のコロンの後が時間
                    parts = line.strip().split(":")
                    if len(parts) > 2:
                        current_time = int(parts[2].strip())
                    else:
                        continue

                timestamps.append(current_time)

            except ValueError as e:
                print(f"Error processing line: {line.strip()}. Error: {e}")
                continue

    # 150ミリ秒以上の一時停止時間をカウント
    for i in range(1, len(timestamps)):
        pause_time = timestamps[i] - timestamps[i - 1]
        if pause_time >= threshold:  # 閾値以上の場合のみカウント
            pause_count += 1

    return pause_count


def calculate_average_pause_time(file_path, threshold=150):
    """
    指定されたファイルから一時停止が閾値（ミリ秒）を超えた平均時間を計算する
    """
    pause_times = []
    last_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            if line.startswith("MOUSE_MOVED") or line.startswith("MOUSE_DRAGGED"):
                try:
                    parts = line.strip().split(":")
                    current_time = int(parts[-2].strip())

                    if last_time is not None:
                        time_elapsed = current_time - last_time
                        if time_elapsed > threshold:
                            pause_times.append(time_elapsed / 1000.0) # ミリ秒から秒に変換

                    last_time = current_time
                except Exception as e:
                    print(f"Error processing line: {line}. Error: {e}")

    average_pause_time = sum(pause_times) / len(pause_times) if pause_times else 0
    return average_pause_time

def calculate_avg_all_sensible_pause_time(file_path, threshold=150):
    """
    指定されたファイルからすべてのイベント間の一時停止時間が
    閾値（ミリ秒）以上の場合のみ、その平均持続時間を算出する

    Parameters:
        file_path (str): ログファイルのパス
        threshold (int): 一時停止時間の閾値（ミリ秒単位、デフォルト: 150）

    Returns:
        float: 閾値以上の一時停止時間の平均持続時間（秒単位）
    """
    timestamps = []
    pause_times = []

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # 特殊ケース: MENU_ITEM_NAVIGATED で "C:\Users" を含む場合
                if line.startswith("MENU_ITEM_NAVIGATED") and "C:\\Users" in line:
                    parts = line.strip().rsplit(":", 1)
                    current_time = int(parts[-1].strip())
                else:
                    # 通常ケース: 2個目のコロンの後が時間
                    parts = line.strip().split(":")
                    if len(parts) > 2:
                        current_time = int(parts[2].strip())
                    else:
                        continue

                timestamps.append(current_time)

            except ValueError as e:
                print(f"Error processing line: {line.strip()}. Error: {e}")
                continue

    # 150ミリ秒以上の一時停止時間をリストに追加
    for i in range(1, len(timestamps)):
        pause_time = timestamps[i] - timestamps[i - 1]
        if pause_time >= threshold:  # 閾値以上の場合のみカウント
            pause_times.append(pause_time / 1000.0)  # ミリ秒から秒に変換

    # 平均持続時間を計算
    average_pause_time = sum(pause_times) / len(pause_times) if pause_times else 0
    return average_pause_time


def calculate_action_pause_time(file_path, actions=("BUTTON_PRESSED", "MENU_ITEM_SELECTED")):
    """
    指定されたファイルからアクション後の一時停止時間の平均を算出する

    Parameters:
        file_path (str): 読み込むファイルのパス
        actions (tuple): 一時停止を計算する対象のアクション

    Returns:
        float: アクション後の一時停止時間の平均
    """
    action_times = []
    pause_times = []

    # ファイルを読み取る
    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # アクション行を特定する
                for action in actions:
                    if action in line:
                        parts = line.strip().split(":")
                        timestamp = int(parts[-1].strip())
                        action_times.append(timestamp)
                        break
            except ValueError:
                print(f"Error processing line: {line}")
                continue

    # 一時停止時間を計算する
    for i in range(1, len(action_times)):
        pause_time = action_times[i] - action_times[i - 1]
        pause_times.append(pause_time / 1000.0)  # ミリ秒から秒に変換

    # 平均を計算する
    average_pause_time = sum(pause_times) / len(pause_times) if pause_times else 0
    return average_pause_time

def calculate_avg_of_all_pauses_time(file_path):
    """
    イベントストリーム内の連続するイベント間の平均一時停止時間を算出する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: すべての連続するイベント間の平均一時停止時間（ミリ秒単位）
    """
    timestamps = []

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # 特殊ケース: MENU_ITEM_NAVIGATED で "C:\\Users" を含む場合
                if line.startswith("MENU_ITEM_NAVIGATED") and "C:\\Users" in line:
                    parts = line.strip().rsplit(":", 1)
                    current_time = int(parts[-1].strip())
                else:
                    # 通常ケース: 2個目のコロンの後が時間
                    parts = line.strip().split(":")
                    if len(parts) > 2:
                        current_time = int(parts[2].strip())
                    else:
                        continue

                timestamps.append(current_time)

            except ValueError as e:
                print(f"Error processing line: {line.strip()}. Error: {e}")
                continue

    # 一時停止時間をリストに追加
    pause_times = [
        (timestamps[i] - timestamps[i - 1]) / 1000.0  # ミリ秒から秒に変換
        for i in range(1, len(timestamps))
    ]

    # 平均持続時間を計算
    average_pause_time = sum(pause_times) / len(pause_times) if pause_times else 0
    return average_pause_time

def calculate_average_mouse_pause_time(file_path, mouse_events=("MOUSE_MOVED", "MOUSE_DRAGGED")):
    """
    指定されたファイルから連続するマウスイベント間の平均一時停止時間を算出する

    Parameters:
        file_path (str): ログファイルのパス
        mouse_events (tuple): 対象となるマウスイベントの種類 (デフォルト: MOUSE_MOVED と MOUSE_DRAGGED)

    Returns:
        float: 平均一時停止時間（ミリ秒単位）
    """
    mouse_timestamps = []
    last_event_type = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # 対象イベントの行を特定
                for event in mouse_events:
                    if event in line:
                        parts = line.strip().split(":")
                        if len(parts) >= 4:  # 行が期待される形式であることを確認
                            timestamp = int(parts[2].strip())  # 3番目のコロン後がタイムスタンプ
                            # 直前のイベントが同じ種類の場合のみタイムスタンプを追加
                            if last_event_type == event:
                                mouse_timestamps.append(timestamp)
                            last_event_type = event
                        break
                    else:
                        last_event_type = None  # 他のイベントが検出されたらリセット
            except ValueError as e:
                print(f"calculate_average_mouse_pause_time_Error processing line: {line.strip()} - Error: {e}")
                continue

    # 一時停止時間を計算
    if len(mouse_timestamps) < 2:
        return 0  # マウスイベントが1つ以下の場合は平均一時停止時間を0とする

    pause_times = [
        (mouse_timestamps[i] - mouse_timestamps[i - 1]) / 1000.0 # ミリ秒から秒に変換
        for i in range(1, len(mouse_timestamps))
    ]

    # 平均を計算
    average_pause_time = sum(pause_times) / len(pause_times)
    return average_pause_time

def calculate_episodes_count(file_path, mouse_events=("MOUSE_MOVED", "MOUSE_DRAGGED"), threshold=150):
    """
    指定されたファイルから連続するマウス移動のエピソード数を算出する

    Parameters:
        file_path (str): ログファイルのパス
        mouse_events (tuple): マウス移動とみなすイベント名 (デフォルト: "MOUSE_MOVED", "MOUSE_DRAGGED")
        threshold (int): エピソードを区切る一時停止時間の閾値 (デフォルト: 150ミリ秒)

    Returns:
        int: マウス移動エピソードの数
    """
    mouse_timestamps = []

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # マウスイベントの行を特定
                if any(event in line for event in mouse_events):
                    parts = line.strip().split(":")
                    if len(parts) >= 3:  # 行が期待される形式であることを確認
                        timestamp = int(parts[2].strip())  # 3番目の部分がタイムスタンプ
                        mouse_timestamps.append(timestamp)
            except ValueError as e:
                print(f"calculate_episodes_count_Error processing line: {line.strip()} - Error: {e}")
                continue

    if not mouse_timestamps:
        return 0  # マウスイベントがなければエピソード数は0

    episodes_count = 1  # 少なくとも1つのエピソードがあると仮定
    for i in range(1, len(mouse_timestamps)):
        # 隣接するタイムスタンプ間の差を計算
        if mouse_timestamps[i] - mouse_timestamps[i - 1] >= threshold:
            episodes_count += 1  # 閾値以上の一時停止があれば新しいエピソードとしてカウント

    return episodes_count


def calculate_average_key_pressed_pause_time(file_path, key_event="KEY_PRESSED"):
    """
    指定されたファイルから連続する KEY_PRESSED イベント間の平均一時停止時間を算出する

    Parameters:
        file_path (str): ログファイルのパス
        key_event (str): 対象となるイベント名 (デフォルト: "KEY_PRESSED")

    Returns:
        float: 平均一時停止時間（ミリ秒単位）
    """
    key_timestamps = []

    with open(file_path, 'r', encoding='utf-8') as file:
        previous_event = None
        for line in file:
            try:
                # KEY_PRESSED イベントの行を特定
                if key_event in line:
                    parts = line.strip().split(":")
                    if len(parts) >= 3:  # 行が期待される形式であることを確認
                        timestamp = int(parts[-1].strip())  # 最後の部分がタイムスタンプ
                        if previous_event == key_event:  # 直前もKEY_PRESSEDの場合のみ追加
                            key_timestamps.append(timestamp)
                        previous_event = key_event
                    else:
                        previous_event = None
                else:
                    previous_event = None  # 他のイベントがあった場合リセット
            except ValueError as e:
                print(f"Error processing line: {line.strip()} - Error: {e}")
                continue

    # 一時停止時間を計算
    if len(key_timestamps) < 2:
        return 0  # KEY_PRESSED イベントが1つ以下の場合は平均一時停止時間を0とする

    # 連続するKEY_PRESSEDイベントの一時停止時間を計算
    pause_times = [
        (key_timestamps[i] - key_timestamps[i - 1]) / 1000.0 # ミリ秒から秒に変換
        for i in range(1, len(key_timestamps))
    ]

    # 平均を計算
    average_pause_time = sum(pause_times) / len(pause_times)
    return average_pause_time


def direction_changes_count(file_path, mouse_events=("MOUSE_MOVED", "MOUSE_DRAGGED")):
    """
    指定されたファイルから移動方向の変化回数を算出する

    Parameters:
        file_path (str): ログファイルのパス
        mouse_events (tuple): マウス移動とみなすイベント名 (デフォルト: "MOUSE_MOVED", "MOUSE_DRAGGED")

    Returns:
        int: マウス移動方向の変化回数
    """
    prev_x, prev_y = None, None
    prev_dx, prev_dy = None, None
    direction_changes = 0

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # マウスイベントの行を特定
                if any(event in line for event in mouse_events):
                    parts = line.strip().split(":")
                    if len(parts) >= 4:  # 行が期待される形式であることを確認
                        coordinates = parts[-1].strip().strip("()").split(",")
                        x, y = int(coordinates[0]), int(coordinates[1])

                        if prev_x is not None and prev_y is not None:
                            dx = x - prev_x
                            dy = y - prev_y

                            # 移動方向の変化を検出 (符号の変化を判定)
                            if (prev_dx is not None and prev_dy is not None) and (
                                (dx != 0 and dx * prev_dx < 0) or
                                (dy != 0 and dy * prev_dy < 0)
                            ):
                                direction_changes += 1

                            # 現在の移動量を保存
                            prev_dx, prev_dy = dx, dy

                        # 現在の座標を保存
                        prev_x, prev_y = x, y

            except ValueError as e:
                print(f"direction_changes_count_Error processing line: {line.strip()} - Error: {e}")
                continue

    return direction_changes

def calculate_total_angle_changes(file_path, mouse_events=("MOUSE_MOVED", "MOUSE_DRAGGED")):
    """
    指定されたファイルから連続するマウス移動間の移動方向角度の変化の合計を算出する

    Parameters:
        file_path (str): ログファイルのパス
        mouse_events (tuple): マウス移動とみなすイベント名 (デフォルト: "MOUSE_MOVED", "MOUSE_DRAGGED")

    Returns:
        float: 移動方向角度の変化の合計（度数単位）
    """
    coordinates = []
    
    # ファイルから座標を抽出
    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # マウスイベントの行を特定
                if any(event in line for event in mouse_events):
                    parts = line.strip().split(":")
                    if len(parts) >= 4:  # 行が期待される形式であることを確認
                        coord_parts = parts[-1].strip().strip("()").split(",")
                        x, y = int(coord_parts[0]), int(coord_parts[1])
                        coordinates.append((x, y))
            except ValueError as e:
                print(f"calculate_total_angle_changes_Error processing line: {line.strip()} - Error: {e}")
                continue

    if len(coordinates) < 3:
        return 0.0  # 少なくとも2つの移動（3点）が必要

    total_angle_change = 0.0

    # 角度の変化を計算
    for i in range(1, len(coordinates) - 1):
        x1, y1 = coordinates[i - 1]
        x2, y2 = coordinates[i]
        x3, y3 = coordinates[i + 1]

        # ベクトル1とベクトル2を計算
        v1 = (x2 - x1, y2 - y1)
        v2 = (x3 - x2, y3 - y2)

        # ベクトルの長さ
        norm_v1 = math.sqrt(v1[0]**2 + v1[1]**2)
        norm_v2 = math.sqrt(v2[0]**2 + v2[1]**2)

        if norm_v1 == 0 or norm_v2 == 0:
            continue  # 移動がない場合はスキップ

        # 内積
        dot_product = v1[0] * v2[0] + v1[1] * v2[1]
        cos_theta = max(min(dot_product / (norm_v1 * norm_v2), 1), -1)  # 数値誤差対策

        # 角度を計算 (ラジアンから度に変換)
        angle_change = math.degrees(math.acos(cos_theta))
        total_angle_change += angle_change

    return total_angle_change

def calculate_avg_menu_item_navigation_time(file_path):
    """
    一回メニューを開いてから何かをメニュー項目を選択するまでの平均時間をカウント
    MENU_ITEM_SELECTEDイベントに対して、2つ目のMOUSE_BUTTON_PRESSEDイベントからの
    ツールチップの表示時間の平均を算出する。ただし直前がKEY_PRESSEDイベントの場合は除外。

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: ツールチップ表示時間の平均（ミリ秒単位）
    """
    tooltip_times = []
    button_pressed_times = []  # MOUSE_BUTTON_PRESSEDイベントのタイムスタンプを格納
    last_event = None  # 直前のイベント名

    with open(file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    # ログを順方向に走査
    for idx, line in enumerate(lines):
        try:
            parts = line.strip().split(":")
            event = parts[0]  # イベント名

            # MOUSE_BUTTON_PRESSEDイベントを検知したらタイムスタンプを保存
            if "MOUSE_BUTTON_PRESSED" in event:
                button_pressed_times.append(int(parts[-1].strip()))
                last_event = "MOUSE_BUTTON_PRESSED"

            # MENU_ITEM_SELECTEDイベントを検知
            elif "MENU_ITEM_SELECTED" in event:
                selected_time = int(parts[-1].strip())

                # 直前のイベントがKEY_PRESSEDの場合は除外
                if last_event == "KEY_PRESSED":
                    continue

                # 2つ目のMOUSE_BUTTON_PRESSEDを探す
                if len(button_pressed_times) >= 2:
                    second_pressed_time = button_pressed_times[-2]
                    tooltip_time = selected_time - second_pressed_time

                    if tooltip_time > 0:  # 正常な時間の場合のみ追加
                        tooltip_times.append(tooltip_time / 1000.0) # ミリ秒から秒に変換

                last_event = "MENU_ITEM_SELECTED"

            # KEY_PRESSEDイベントを検知
            elif "KEY_PRESSED" in event:
                last_event = "KEY_PRESSED"

        except ValueError as e:
            print(f"Error processing line: {line.strip()}. Error: {e}")
            continue

    # 平均表示時間を計算
    avg_tooltip_time = sum(tooltip_times) / len(tooltip_times) if tooltip_times else 0
    return avg_tooltip_time

def calculate_avg_menu_navigation_time(file_path):
    """
    MENU_ITEM_NAVIGATEDイベントから次のイベントまでの時間の平均を算出する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: MENU_ITEM_NAVIGATEDから次のイベントまでの平均時間（ミリ秒単位）
    """
    tooltip_times = []  # ツールチップ表示時間を格納するリスト
    last_navigated_time = None  # MENU_ITEM_NAVIGATEDのタイムスタンプ

    with open(file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    for idx, line in enumerate(lines):
        try:
            parts = line.strip().split(":")
            if len(parts) < 3:
                continue  # 不正な行はスキップ

            event = parts[0].strip()  # イベント名
            current_time = None

            # MOUSE_MOVEDやその他の行からタイムスタンプを正確に抽出
            if "MOUSE_MOVED" in event or "MOUSE_DRAGGED" in event:
                current_time = int(parts[2].strip())  # 3番目の部分がタイムスタンプ

            elif event == "MENU_ITEM_NAVIGATED":
                current_time = int(parts[-1].strip())  # 最後の部分がタイムスタンプ
                last_navigated_time = current_time  # MENU_ITEM_NAVIGATEDの時間を記録

            # MENU_ITEM_NAVIGATEDから次のイベントの時間差を計算
            if current_time is not None and last_navigated_time is not None:
                tooltip_time = current_time - last_navigated_time
                if tooltip_time > 0:  # 正の時間のみカウント
                    tooltip_times.append(tooltip_time / 1000.0) # ミリ秒から秒に変換
                    last_navigated_time = None  # 次のMENU_ITEM_NAVIGATEDに備える

        except ValueError as e:
            print(f"Error processing line: {line.strip()}. Error: {e}")
            continue

    # 平均時間を算出
    avg_tooltip_time = sum(tooltip_times) / len(tooltip_times) if tooltip_times else 0
    return avg_tooltip_time

def calculate_menu_viewing_sessions_count(file_path):
    """
    一回メニューを開いてから何かをメニュー項目を選択するまでのセッションの数をカウント

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        int: メニュー表示セッションの回数
    """
    session_count = 0
    button_pressed_times = []  # MOUSE_BUTTON_PRESSEDイベントのタイムスタンプを格納
    last_event = None  # 直前のイベント名

    with open(file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    # ログを順方向に走査
    for idx, line in enumerate(lines):
        try:
            parts = line.strip().split(":")
            event = parts[0]  # イベント名

            # MOUSE_BUTTON_PRESSEDイベントを検知してタイムスタンプを保存
            if "MOUSE_BUTTON_PRESSED" in event:
                button_pressed_times.append(int(parts[-1].strip()))
                last_event = "MOUSE_BUTTON_PRESSED"

            # MENU_ITEM_SELECTEDイベントを検知
            elif "MENU_ITEM_SELECTED" in event:
                selected_time = int(parts[-1].strip())

                # 直前のイベントがKEY_PRESSEDの場合は無視する
                if last_event == "KEY_PRESSED":
                    continue

                # 2つ目のMOUSE_BUTTON_PRESSEDがある場合、セッションとしてカウント
                if len(button_pressed_times) >= 2:
                    session_count += 1
                    # 2つ目のMOUSE_BUTTON_PRESSEDイベント以降のセッションが終わったとみなす
                    button_pressed_times.clear()

                last_event = "MENU_ITEM_SELECTED"

            # KEY_PRESSEDイベントを検知したら状態をリセット
            elif "KEY_PRESSED" in event:
                last_event = "KEY_PRESSED"

        except ValueError as e:
            print(f"Error processing line: {line.strip()}. Error: {e}")
            continue

    return session_count

def calculate_menu_item_navigations_count(file_path):
    """
    指定されたファイルからMENU_ITEM_NAVIGATEDイベントの数をカウントする

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        int: MENU_ITEM_NAVIGATEDイベントの発生回数
    """
    count = 0  # カウント用変数

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # MENU_ITEM_NAVIGATEDイベントの行を検出
                if "MENU_ITEM_NAVIGATED" in line:
                    count += 1
            except Exception as e:
                print(f"Error processing line: {line.strip()}. Error: {e}")
                continue

    return count

def calculate_avg_speed_before_button_clicks(file_path, time_window=500):
    """
    MOUSE_BUTTON_PRESSED直前のマウスの平均速度を算出する

    Parameters:
        file_path (str): ログファイルのパス
        time_window (int): 直前の時間ウィンドウ（ミリ秒単位、デフォルト: 500）

    Returns:
        float: MOUSE_BUTTON_PRESSED直前のマウスの平均速度（ピクセル/秒）
    """
    import math

    speeds = []
    mouse_moves = []  # MOUSE_MOVEDイベントのデータ (time, position)
    last_button_pressed_time = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                parts = line.strip().split(":")
                event = parts[0]

                # MOUSE_MOVEDイベントを処理して、時間と位置を記録
                if event == "MOUSE_MOVED":
                    time = int(parts[-2].strip())  # 時間
                    x, y = map(int, parts[-1].strip().strip("()").split(","))
                    mouse_moves.append((time, x, y))

                # MOUSE_BUTTON_PRESSEDイベントを検知
                elif event == "MOUSE_BUTTON_PRESSED" and "BUTTON1" in line:
                    current_time = int(parts[-1].strip())  # ボタンを押した時刻
                    total_distance = 0.0
                    total_time = 0.0

                    # 直前のtime_window内のMOUSE_MOVEDデータを探す
                    for i in range(len(mouse_moves) - 1, -1, -1):
                        move_time, move_x, move_y = mouse_moves[i]
                        if current_time - move_time <= time_window:
                            if i > 0:
                                prev_time, prev_x, prev_y = mouse_moves[i - 1]
                                distance = math.sqrt((move_x - prev_x) ** 2 + (move_y - prev_y) ** 2)
                                time_diff = (move_time - prev_time) / 1000.0  # ミリ秒から秒に変換

                                if time_diff > 0:
                                    total_distance += distance
                                    total_time += time_diff
                        else:
                            break

                    # 平均速度を計算して保存
                    avg_speed = total_distance / total_time if total_time > 0 else 0
                    speeds.append(avg_speed)

            except Exception as e:
                print(f"Error processing line: {line.strip()}. Error: {e}")

    # 平均速度を計算して返す
    overall_avg_speed = sum(speeds) / len(speeds) if speeds else 0
    return overall_avg_speed

def calculate_avg_items_navigated_in_each_session(file_path):
    """
    MENU_ITEM_SELECTEDイベントに対して、それ以前の2つ目のMOUSE_BUTTON_PRESSEDイベントから
    MENU_ITEM_SELECTEDイベントまでの間に出現するMENU_ITEM_NAVIGATEDイベントの数をカウントし、
    その平均数を算出する

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: 各メニュー操作セッションでのMENU_ITEM_NAVIGATEDイベントの平均数
    """
    session_item_counts = []  # セッションごとのMENU_ITEM_NAVIGATEDの数を格納
    button_pressed_times = []  # MOUSE_BUTTON_PRESSEDイベントのタイムスタンプを格納

    with open(file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    for idx, line in enumerate(lines):
        try:
            parts = line.strip().split(":")
            event = parts[0]  # イベント名

            # MOUSE_BUTTON_PRESSEDイベントのタイムスタンプを保存
            if "MOUSE_BUTTON_PRESSED" in event:
                timestamp = int(parts[-1].strip())
                button_pressed_times.append((idx, timestamp))

            # MENU_ITEM_SELECTEDイベントの処理
            elif "MENU_ITEM_SELECTED" in event:
                selected_time = int(parts[-1].strip())

                # 2つ目のMOUSE_BUTTON_PRESSEDを探す
                if len(button_pressed_times) >= 2:
                    second_pressed_index = button_pressed_times[-2][0]  # 2つ目のMOUSE_BUTTON_PRESSEDのインデックス
                    current_item_count = 0

                    # 2つ目のMOUSE_BUTTON_PRESSEDからMENU_ITEM_SELECTEDまでのMENU_ITEM_NAVIGATEDをカウント
                    for i in range(second_pressed_index, idx):
                        if "MENU_ITEM_NAVIGATED" in lines[i]:
                            current_item_count += 1

                    # カウントをリストに追加
                    session_item_counts.append(current_item_count)

        except ValueError as e:
            print(f"Error processing line: {line.strip()}. Error: {e}")
            continue

    # 平均数の計算
    avg_items_navigated = sum(session_item_counts) / len(session_item_counts) if session_item_counts else 0
    return avg_items_navigated

def calculate_avg_selected_menu_items_dwell_time(file_path):
    """
    MENU_ITEM_SELECTEDイベントが発生する前の、対応するMENU_ITEM_NAVIGATEDイベントからの静止時間の平均を算出する。
    直前のイベントがKEY_PRESSEDの場合は除外する。

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: MENU_ITEM_NAVIGATEDからMENU_ITEM_SELECTEDまでの平均時間（秒単位）
    """
    dwell_times = []  # 静止時間を格納するリスト
    navigated_timestamps = {}  # MENU_ITEM_NAVIGATEDのタイムスタンプをイベント名でマッピング
    last_event = None  # 直前のイベント

    with open(file_path, 'r', encoding='utf-8') as file:
        lines = file.readlines()

    # ログを順方向に走査
    for line in lines:
        try:
            parts = line.strip().split(":")
            # if len(parts) < 3:
            #     continue  # 正しいフォーマットでない行はスキップ

            event = parts[0]  # イベント名
            event_content = parts[1].strip() if len(parts) > 2 else ""  # イベント内容

            if "MENU_ITEM_NAVIGATED" in event and "C:\\Users" in line:
                timestamp = int(parts[-1].strip())

            else:
                timestamp = int(parts[2].strip())  # 二つ目の「:」の後が時間

            # MENU_ITEM_NAVIGATEDイベントを検知し、イベント内容ごとにタイムスタンプを保存
            if "MENU_ITEM_NAVIGATED" in event:
                navigated_timestamps[event_content] = timestamp
                last_event = "MENU_ITEM_NAVIGATED"

            # KEY_PRESSEDイベントを検知
            elif "KEY_PRESSED" in event:
                last_event = "KEY_PRESSED"

            # MENU_ITEM_SELECTEDイベントを検知
            elif "MENU_ITEM_SELECTED" in event:
                if last_event == "KEY_PRESSED":
                    # 直前がKEY_PRESSEDの場合はスキップ
                    last_event = "MENU_ITEM_SELECTED"
                    continue

                if event_content in navigated_timestamps:
                    # 対応するMENU_ITEM_NAVIGATEDのタイムスタンプを取得
                    start_time = navigated_timestamps[event_content]
                    dwell_time = timestamp - start_time  # 静止時間を算出

                    if dwell_time > 0:  # 正の時間のみ追加
                        dwell_times.append(dwell_time / 1000.0) # ミリ秒から秒に変換

                    # 1回のMENU_ITEM_SELECTEDに対応するMENU_ITEM_NAVIGATEDをリセット
                    del navigated_timestamps[event_content]

                last_event = "MENU_ITEM_SELECTED"

        except (ValueError, IndexError) as e:
            print(f"Error processing line: {line.strip()}. Error: {e}")
            continue

    # 平均静止時間を計算
    avg_dwell_time = sum(dwell_times) / len(dwell_times) if dwell_times else 0
    return avg_dwell_time

def calculate_avg_combo_selection_time(file_path):
    """
    ログファイル内のCOMPONENT_FOCUS_GAINEDイベントから、それ以降の最初のCOMPONENT_FOCUS_LOSTイベントまでの
    平均時間を算出する。

    Parameters:
        file_path (str): ログファイルのパス

    Returns:
        float: COMPONENT_FOCUS_GAINEDからCOMPONENT_FOCUS_LOSTまでの平均時間（秒単位）
    """
    focus_times = []
    focus_gained_timestamp = None

    with open(file_path, 'r', encoding='utf-8') as file:
        for line in file:
            try:
                # COMPONENT_FOCUS_GAINED イベントを検知
                if "COMPONENT_FOCUS_GAINED" in line:
                    parts = line.strip().split(":")
                    if len(parts) > 3:
                        focus_gained_timestamp = int(parts[2].strip())

                # COMPONENT_FOCUS_LOST イベントを検知
                elif "COMPONENT_FOCUS_LOST" in line and focus_gained_timestamp is not None:
                    parts = line.strip().split(":")
                    if len(parts) > 3:
                        focus_lost_timestamp = int(parts[2].strip())
                        focus_time = focus_lost_timestamp - focus_gained_timestamp
                        if focus_time > 0:
                            focus_times.append(focus_time / 1000.0) # ミリ秒から秒に変換
                        focus_gained_timestamp = None  # リセット

            except ValueError as e:
                print(f"Error processing line: {line.strip()}. Error: {e}")
                continue

    # 平均時間を計算
    average_focus_time = sum(focus_times) / len(focus_times) if focus_times else 0
    return average_focus_time

def process_logs(base_folder_path, output_file):
    """
    各フォルダのログファイルを処理し、総移動距離、平均速度、全体の時間、平均アクション一時停止時間、
    平均マウス一時停止時間、平均キー押下一時停止時間、マウス移動エピソード数、方向変化回数、
    角度変化の合計、X方向とY方向の平均速度などを計算して保存する
    """
    results = []

    for i in range(1, 26):  # フォルダ番号の範囲を指定（例: 1〜25）
        subject_number = f"{i:02d}"
        folder_path = os.path.join(base_folder_path, subject_number, "logs")

        if os.path.exists(folder_path):
            log_files = [file for file in os.listdir(folder_path) if file.startswith("ui-log") and file.endswith(".txt")]
            # 日付の昇順でソート
            log_files.sort()

            for index, file_name in enumerate(log_files):
                file_path = os.path.join(folder_path, file_name)
                total_distance = calculate_distance(file_path)
                average_speed = calculate_average_speed(file_path)
                max_speed = calculate_max_speed(file_path)
                total_time = calculate_total_time(file_path)
                mouse_sensible_pause_count = calculate_mouse_sensible_pause_count(file_path)
                average_pause_time = calculate_average_pause_time(file_path)

                average_absolute_acceleration = calculate_average_absolute_acceleration(file_path)
                max_acceleration = calculate_max_acceleration(file_path)
                min_acceleration = calculate_min_acceleration(file_path)
                action_pause_time = calculate_action_pause_time(file_path)
                avg_of_all_pauses_time = calculate_avg_of_all_pauses_time(file_path)
                mouse_pause_time = calculate_average_mouse_pause_time(file_path)
                key_pause_time = calculate_average_key_pressed_pause_time(file_path)
                episodes_count = calculate_episodes_count(file_path)
                direction_changes = direction_changes_count(file_path)
                total_angle_changes = calculate_total_angle_changes(file_path)
                average_x_speed = calculate_average_X_direction_speed(file_path)
                average_y_speed = calculate_average_Y_direction_speed(file_path)
                average_x_accel = avg_mouse_X_accel(file_path)
                average_y_accel = avg_mouse_Y_accel(file_path)
                max_x_speed = calculate_max_x_speed(file_path)
                max_y_speed = calculate_max_y_speed(file_path)
                max_x_accel = calculate_max_x_accel(file_path)
                max_y_accel = calculate_max_y_accel(file_path)
                avg_all_sensible_pause_time = calculate_avg_all_sensible_pause_time(file_path)
                all_sensible_pause_count = calculate_all_sensible_pause_count(file_path)
                avg_speed_before_button_clicks = calculate_avg_speed_before_button_clicks(file_path)
                avg_menu_item_navigation_time = calculate_avg_menu_item_navigation_time(file_path)
                avg_menu_navigation_time = calculate_avg_menu_navigation_time(file_path)
                menu_item_navigations_count = calculate_menu_item_navigations_count(file_path)
                menu_viewing_sessions_count = calculate_menu_viewing_sessions_count(file_path)
                avg_items_navigated_in_each_session = calculate_avg_items_navigated_in_each_session(file_path)
                avg_selected_menu_items_dwell_time = calculate_avg_selected_menu_items_dwell_time(file_path)
                avg_combo_selection_time = calculate_avg_combo_selection_time(file_path)

                # Taskの決定
                if index == 0:
                    task = "training"
                else:
                    task = f"task_{index:02d}"

                results.append((
                    subject_number, file_name, task, total_distance, average_speed, max_speed, 
                    total_time, mouse_sensible_pause_count, average_pause_time, 
                    average_absolute_acceleration, max_acceleration, min_acceleration, 
                    action_pause_time, avg_of_all_pauses_time, mouse_pause_time, key_pause_time, episodes_count, 
                    direction_changes, total_angle_changes, average_x_speed, average_y_speed,
                    average_x_accel, average_y_accel, max_x_speed, max_y_speed,
                    max_x_accel, max_y_accel, avg_all_sensible_pause_time, all_sensible_pause_count,
                    avg_speed_before_button_clicks, avg_menu_item_navigation_time, avg_menu_navigation_time,
                    menu_item_navigations_count, menu_viewing_sessions_count, avg_items_navigated_in_each_session,
                    avg_selected_menu_items_dwell_time, avg_combo_selection_time
                ))

    # 結果をファイルに保存
    with open(output_file, 'w', encoding='utf-8') as output:
        output.write("Subject,File,Task,Total_Distance,Average_Mouse_Speed,Max_Speed,Total_Time,Mouse_Sensible_Pause_Count,Average_Pause_Time,Average_Absolute_Acceleration,Max_Acceleration,Min_Acceleration,Action_Pause_Time,Avg_of_All_Pauses_Time,Mouse_Pause_Time,Key_Pause_Time,Episodes_Count,Direction_Changes,Total_Angle_Changes,Average_X_Direction_Speed,Average_Y_Direction_Speed,Average_X_Accel,Average_Y_Accel,Max_X_Speed,Max_Y_Speed,Max_X_Accel,Max_Y_Accel,Avg_All_Sensible_Pause_Time,All_Sensible_Pause_Count,Avg_Speed_Before_Button_Clicks,Avg_Menu_Item_Navigation_Time,Avg_Menu_Navigation_Time,Menu_Item_Navigations_Count,Menu_Viewing_Sessions_Count,Avg_Items_Navigated_in_Each_Session,Avg_Selected_Menu_Items_Dwell_Time,Avg_Combo_Selection_Time\n")
        for (subject, file_name, task, distance, speed, max_speed, time, mouse_sensible_pause_count, 
             avg_pause_time, absolute_acceleration, max_acc, min_acc, 
             action_pause_time, avg_of_all_pauses_time, mouse_pause_time, key_pause_time, episodes_count, 
             direction_changes, total_angle_changes, average_x_speed, average_y_speed,
             average_x_accel, average_y_accel, max_x_speed, max_y_speed,
             max_x_accel, max_y_accel, avg_all_sensible_pause_time, all_sensible_pause_count,
             avg_speed_before_button_clicks, avg_menu_item_navigation_time,avg_menu_navigation_time, 
             menu_item_navigations_count, menu_viewing_sessions_count, avg_items_navigated_in_each_session,
             avg_selected_menu_items_dwell_time, avg_combo_selection_time) in results:
            output.write(f"{subject},{file_name},{task},{distance:.2f},{speed:.2f},{max_speed:.2f},{time},{mouse_sensible_pause_count},{avg_pause_time:.2f},{absolute_acceleration:.2f},{max_acc:.2f},{min_acc:.2f},{action_pause_time:.2f},{avg_of_all_pauses_time:.2f},{mouse_pause_time:.2f},{key_pause_time:.2f},{episodes_count},{direction_changes},{total_angle_changes:.2f},{average_x_speed:.2f},{average_y_speed:.2f},{average_x_accel:.2f},{average_y_accel:.2f},{max_x_speed:.2f},{max_y_speed:.2f},{max_x_accel:.2f},{max_y_accel:.2f},{avg_all_sensible_pause_time:.2f},{all_sensible_pause_count},{avg_speed_before_button_clicks:.2f},{avg_menu_item_navigation_time:.2f},{avg_menu_navigation_time:.2f},{menu_item_navigations_count},{menu_viewing_sessions_count},{avg_items_navigated_in_each_session:.2f},{avg_selected_menu_items_dwell_time:.2f},{avg_combo_selection_time:.2f}\n")

    print(f"結果を {output_file} に保存しました。")


In [36]:
# ベースフォルダのパスと出力ファイル名を指定
base_folder_path = r".\SubjectData"
output_file = "ui_log_features.csv"

process_logs(base_folder_path, output_file)


Distance: 6.324555320336759, Time Elapsed: 1.456
Distance: 19.235384061671343, Time Elapsed: 0.008
Distance: 43.382023926967726, Time Elapsed: 0.008
Distance: 65.92419889539804, Time Elapsed: 0.008
Distance: 84.50443775329198, Time Elapsed: 0.008
Distance: 101.95096860746347, Time Elapsed: 0.008
Distance: 105.1094667477673, Time Elapsed: 0.008
Distance: 111.23398761170077, Time Elapsed: 0.008
Distance: 108.4665847162157, Time Elapsed: 0.008
Distance: 114.56002793295748, Time Elapsed: 0.008
Distance: 110.85576214162258, Time Elapsed: 0.008
Distance: 109.88175462741756, Time Elapsed: 0.008
Distance: 104.1393297462587, Time Elapsed: 0.008
Distance: 102.59142264341595, Time Elapsed: 0.008
Distance: 97.67292357659824, Time Elapsed: 0.008
Distance: 91.92388155425118, Time Elapsed: 0.008
Distance: 85.98837130682264, Time Elapsed: 0.008
Distance: 119.28118040998756, Time Elapsed: 15.946
Distance: 111.75866856758807, Time Elapsed: 0.005
Distance: 113.13708498984761, Time Elapsed: 0.008
Distance